In [1]:
import numpy as np
import h5py,glob
from pycbc import conversions

import matplotlib as mpl
import matplotlib.pyplot as plt

mpl.use('pgf')
pgf_with_custom_preamble = {
    "text.usetex": True,    # use inline math for ticks
    "pgf.texsystem" : "pdflatex"
}
mpl.rcParams.update(pgf_with_custom_preamble)

In [2]:
#path = ['/work/yifan.wang/4ogc/release_prod/shichao_extract/',
#        '/work/yifan.wang/4ogc/release_prod/yifan/',
#        '/work/yifan.wang/4ogc/release_prod/shilpa/',
#        '/work/yifan.wang/4ogc/release_prod/sumit/']
#path = ['/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/']
path = ['/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/']
posfile = []
for p in path:
    f = glob.glob(p+'/*.hdf')
    posfile.extend(f)

In [3]:
def custom_sort(name):
    return name.split('GW')[1][:13]
#the 0th is dot, 1st is person name, 2nd is GW event name

def extract_quantile(sample):
    return np.quantile(sample,0.5), np.quantile(sample,0.95) - np.quantile(sample,0.5), \
                                             np.quantile(sample,0.5) - np.quantile(sample,0.05)
def latexpm(num,p,m,nround=1):
    if nround == 0:
        num,p,m = round(num),round(p),round(m)
    else:
        num,p,m = round(num,nround),round(p,nround),round(m,nround)
    return str(r'$'+str(num)+r'^{+'+str(p)+r'}_{-'+str(m)+r'}$')

In [4]:
posfile.sort(key=custom_sort)

In [5]:
#posfile=posfile[:2]

In [6]:
m1 = []
m2 = []
chi_eff = []
dist = []
labels = []

for i,path in enumerate(posfile):
    f = h5py.File(path,'r')
    #print('Analyzing the '+str(i)+'th event:'+path)
    
    #m1,m2,mc,q
    m1.append(f['samples']['srcmass1'][()])
    m2.append(f['samples']['srcmass2'][()])
    chi_eff.append(f['samples']['chi_eff'][()])
    dist.append(f['samples']['distance'][()])
    labels.append('GW'+path.split('GW')[1][:13])

    f.close()

In [7]:
len(labels)

7

In [8]:
posfile

['/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW191224_043228.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200106_134123.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200129_114245.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200210_005122.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200214_223307.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200305_084739.hdf',
 '/work/yifan.wang/4ogc/release_prod/convertsnr/newevents/GW200318_191337.hdf']

In [9]:
color = ['tab:blue', 'tab:orange', 'tab:purple', 'tab:brown', \
         'tab:pink', 'tab:gray','tab:cyan']
#'tab:olive',
alpha = [0.55,0.5,0.45,0.4,0.35,0.3]
#alpha = [0.4,0.4,0.4,0.4,0.4]

def dividesix(i):
    return 0,0

In [10]:
#fig = plt.figure(figsize=(15, 15*(np.sqrt(5)-1.0)/2.0));

fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

mpl.rcParams.update({'axes.labelsize': 24,'ytick.labelsize': 22,'xtick.labelsize':16})
fig = plt.figure(figsize=(fig_width*2,fig_height))
#mpl.rcParams.update({'axes.labelsize': 18,'ytick.labelsize': 12,'xtick.labelsize':12})
#ytick label size: 
#fig = plt.figure(figsize=(fig_width,fig_width/golden_mean))
#ax m1
ax = fig.add_subplot(141);
#bx m2
bx = fig.add_subplot(142);
#cx chieff
cx = fig.add_subplot(143);
#dx d
dx = fig.add_subplot(144);

def set_axis_style(ax, labels,hide=False):
    for i,contents in enumerate(labels):
        labels[i] = str(7-i)+ ':\t'+contents
    ax.get_yaxis().set_tick_params(direction='out')
    ax.yaxis.set_ticks_position('left')
    ax.set_yticks(np.arange(1, len(labels) + 1))
    if hide==True:
        ax.set_yticklabels([])
    else:
        ax.set_yticklabels(labels)
    ax.set_ylim(0.25, len(labels) + 0.75)
    #ax.set_xlabel('Gravitational-Wave Events')

def plotviolin(idx,par,plot_bns_distance_bar=False):
    violinparts = idx.violinplot(par[::-1], 
          showmeans=False, 
          showmedians=False, 
          showextrema=False, 
          vert=False, 
          widths=0.8)
    #color
    for i,pc in enumerate(violinparts['bodies']):
        ind1,ind2 = dividesix(i)
        pc.set_facecolor(color[ind1])
        pc.set_edgecolor(color[ind1])
        pc.set_alpha(alpha[0])
    
    #for b in violinparts['bodies']:
    # get the center
        #m = np.mean(b.get_paths()[0].vertices[:, 1])
    # modify the paths to not go further right than the center
        #b.get_paths()[0].vertices[:, 1] = np.clip(b.get_paths()[0].vertices[:, 1], m,np.inf)
        #b.set_color('b')
        
    for i,d in enumerate(par[::-1]):
        if labels[::-1][i] == 'GW170817_124104' or labels[::-1][i] == 'GW190425_081805':
            if plot_bns_distance_bar == False:
                continue
        med = np.median(d)
     #print i,x                 
        low,upp = np.percentile(d,[5]),np.percentile(d,[95])
        err_low= np.abs(med-low)
        err_high = np.abs(upp - med)
        ind1,ind2 = dividesix(i)
        idx.errorbar(med,i+1,xerr=[err_low,err_high],ecolor=color[ind1],alpha=0.5,
                        marker=None, capthick=2, capsize=8, linewidth=0.01)
#######################################################################################
plotviolin(ax,m1)
#plot GW name
set_axis_style(ax, labels[::-1])
ax.set_xscale('log')
ax.set_xlabel(r'$m_1 ~/~M_\odot$')
ax.set_xlim(1,400)

for i,x in enumerate(ax.get_yticklabels()):
    ind1,ind2 = dividesix(i)
    x.set_color(color[ind1])
    
plotviolin(bx,m2)
bx.set_xlabel(r'$m_2 ~/~M_\odot$')
bx.set_xlim(1,150)
bx.set_xscale('log')
set_axis_style(bx, labels[::-1],hide=True)

plotviolin(cx,chi_eff)
cx.set_xlabel(r'$\chi_\mathrm{eff}$')
set_axis_style(cx, labels[::-1],hide=True)    
cx.set_xlim(-1,1)

plotviolin(dx,dist,plot_bns_distance_bar=True)
dx.set_xlabel(r'$D_\mathrm{L}~/~\mathrm{Mpc}$')
dx.set_xscale('log')
dx.set_xlim(20,20000)
set_axis_style(dx, labels[::-1],hide=True) 

for i in [ax,bx,cx,dx]:
    if i==cx:
        alpha=0.5
    else:
        alpha=0.35
    i.xaxis.grid(True,ls='--',which='both',alpha=alpha)
fig.subplots_adjust(wspace=0.1)
fig.savefig('pe_newevents.pdf', backend='pgf',bbox_inches='tight')